<a href="https://colab.research.google.com/github/dgg32/db_kepler/blob/master/kepler_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install keplergl

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 9.7 MB 4.9 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 1.0 MB 48.4 MB/s 
     |████████████████████████████████| 16.7 MB 45.1 MB/s 
     |████████████████████████████████| 6.3 MB 47.2 MB/s 
  Using cached jedi-0.18.1-py2.py3-none-any.whl (1.6 MB)
  Created wheel for keplergl: filename=keplergl-0.3.2-py2.py3-none-any.whl size=17922343 sha256=29101ba046c108ba897b6d0a6244c7f4b8f0029c2c15f82e8abcd53d78d952e6
  Stored in directory: /root/.cache/pip/wheels/4b/19/e5/0852b7888ee350e9c57087ccc61eeab9daf50f5caac9c690ec
Successfully built keplergl


In [47]:
from keplergl import KeplerGl
import pandas as pd
import requests
from google.colab import output
from datetime import datetime
output.enable_custom_widget_manager()
import os
from getpass import getpass
Client_Id = getpass('Enter DB API Client_Id: ')
Api_Key = getpass('Enter DB API Api_Key: ')


Enter DB API Client_Id: ··········
Enter DB API Api_Key: ··········


In [48]:
if not os.path.exists("data"):
    os.mkdir("data")


In [49]:
bahnhof = pd.read_csv("https://raw.githubusercontent.com/dgg32/db_kepler/master/data/bahnhof.csv")
bahnhof.head()

EVA_NR DS100               NAME  Verkehr  longitude   latitude  \
0  8001944  TETN      Eutingen Nord       RV   8.753100  48.484700   
1  8003074   MIA    Ingolstadt Audi       RV  11.407456  48.790496   
2  8001510  TDSA   Dornstetten-Aach       RV   8.482910  48.473300   
3  8001966  MFOL         Feldolling  nur DPN  11.852244  47.895336   
4  8002535  EOBG  Halver-Oberbrügge       RV   7.574042  51.191867   

                 state  
0    Baden-Württemberg  
1               Bayern  
2    Baden-Württemberg  
3               Bayern  
4  Nordrhein-Westfalen

In [50]:
bahnhof[bahnhof["NAME"] == "Hamburg Hbf"]["DS100"].values[0]

'AH'

In [51]:
def search_route(start, end, time, time_type):
    #curl -X POST -H "Accept: application/json" -H "Content-Type: application/json" 
    #"https://openapi.trassenfinder.de/3.12/api/v5/routen/suche"  
    # -d '{"infrastruktur_id": 10, "sucheinstellungen": {"an_abzeit": "2022-11-13T16:38:36+02:00", "verkehrsart": "spfv_lok", "zeitvorgabe_typ": "abzeit"},  
    # "wegpunkte": [{"betriebsstelle": {"ds100": "HBS"}}, {"betriebsstelle": {"ds100":"MH"}}]}'
    start_ds100 = bahnhof[bahnhof["NAME"] == start]["DS100"].values[0]
    end_ds100 = bahnhof[bahnhof["NAME"] == end]["DS100"].values[0]

    headers = {'Accept': 'application/json', 'Content-Type': 'application/json'}
    data = {"infrastruktur_id": 10, "sucheinstellungen": {"an_abzeit": time, "verkehrsart": "spfv_lok", "zeitvorgabe_typ": time_type},  
    "wegpunkte": [{"betriebsstelle": {"ds100": start_ds100}}, {"betriebsstelle": {"ds100":end_ds100}}]}

    #print (data)

    r = requests.post('https://openapi.trassenfinder.de/3.12/api/v5/routen/suche', headers=headers, json=data)

    return r.json()

In [52]:
route = search_route("Braunschweig Hbf", "München Hbf", "2022-11-09T07:16:36+02:00", "abzeit")

In [53]:
route["result"]["gewichtete_route"]["routenpunkte"][:5]

[{'ds100': 'HBS',
  'wegpunkt_index': 0,
  'naechstes_streckensegment': {'von': 'HBS',
   'bis': 'HGAA',
   'streckennummer': 1730},
  'laufende_hm': 0,
  'technische_fahrzeit_info': {'ankunft_min': 0, 'abfahrt_min': 0},
  'geschwindigkeit_technisch_hmh': 929,
  'haltart': 'kundenhalt',
  'halteplatz_sprungart': 'durchbindung',
  'schiebelok_kupplungsart': 'nichts',
  'verkehrshalt_trotz_fehlendem_bahnsteig': False,
  'halteplatz_zu_kurz': False,
  'gleiswechselbetrieb': False,
  'begegnungsverbot': False,
  'energieverbrauch_info': {'energieverbrauch_traktion_kwh': 0,
   'energieverbrauch_hilfsbetriebe_kwh': 0,
   'energieverbrauch_wagen_kwh': 0,
   'energieverbrauch_gesamt_kwh': 0},
  'energieverbrauch_kosten_euro': 0,
  'marktsegmente': [],
  'trassenpreis_euro': 0,
  'stationspreis_euro': 56,
  'kosten_fahrzeuge_personal_euro': 0,
  'nachschiebekosten_euro': 0,
  'strecke_info': {'ausserhalb_db_netz': False,
   'ungeprueft_kv': False,
   'ungeprueft_streckenklasse': False,
   'unge

In [54]:
source_lat = -1000
source_lng = -1000

target_lat = -1000
target_lng = -1000

previous_station = ""

cumulative_time = 0

cumulative_energy = 0

cumulative_distance = 0

content = ",".join(["source_lat", "source_lng", "target_lat", "target_lng", "from_to", "cumulative_distance_km", "cumulative_energy_kwh", "cumulative_min"]) + "\n"

#route["result"]["gewichtete_route"]["routenpunkte"]
for s in route["result"]["gewichtete_route"]["routenpunkte"]:
    ds100 = s["ds100"]
    #print (s["technische_fahrzeit_info"])
    if source_lat == -1000:
        try:
            source_lat = bahnhof[bahnhof["DS100"] == ds100]["latitude"].values[0]
            source_lng = bahnhof[bahnhof["DS100"] == ds100]["longitude"].values[0]
            previous_station = bahnhof[bahnhof["DS100"] == ds100]["NAME"].values[0]
            #distance = s["laufende_hm"] - cumulative_distance
            cumulative_distance = s["laufende_hm"]/10

            #energy = s["energieverbrauch_info"]["energieverbrauch_gesamt_kwh"] - cumulative_energy
            cumulative_energy = s["energieverbrauch_info"]["energieverbrauch_gesamt_kwh"]

            cumulative_time = s["technische_fahrzeit_info"]["ankunft_min"]

            content += f"{source_lat},{source_lng},{source_lat},{source_lng},{previous_station},{cumulative_distance},{cumulative_energy},{cumulative_time}\n"

        except:
            pass
    else:
        try:


            target_lat = bahnhof[bahnhof["DS100"] == ds100]["latitude"].values[0]
            target_lng = bahnhof[bahnhof["DS100"] == ds100]["longitude"].values[0]
            

            #distance = s["laufende_hm"] - cumulative_distance
            cumulative_distance = s["laufende_hm"]/10

            #energy = s["energieverbrauch_info"]["energieverbrauch_gesamt_kwh"] - cumulative_energy
            cumulative_energy = s["energieverbrauch_info"]["energieverbrauch_gesamt_kwh"]

            cumulative_time = s["technische_fahrzeit_info"]["ankunft_min"]
            current_station = bahnhof[bahnhof["DS100"] == ds100]["NAME"].values[0]

            from_to = f"{previous_station} -> {current_station}"
            previous_station = current_station
            
            content += f"{source_lat},{source_lng},{target_lat},{target_lng},{from_to},{cumulative_distance},{cumulative_energy},{cumulative_time}\n"

            source_lat = target_lat
            source_lng = target_lng
        except:
            pass


with open("data/data_route.csv", "w") as output:
    output.write(content)

In [55]:
route_df = pd.read_csv("data/data_route.csv")
route_df.head()

source_lat  source_lng  target_lat  target_lng  \
0   52.252218   10.540295   52.252218   10.540295   
1   52.252218   10.540295   52.257212   10.359760   
2   52.257212   10.359760   52.318942   10.232145   
3   52.318942   10.232145   52.335731   10.167325   
4   52.335731   10.167325   52.354704   10.110601   

                        from_to  cumulative_distance_km  \
0              Braunschweig Hbf                     0.0   
1  Braunschweig Hbf -> Vechelde                    15.0   
2             Vechelde -> Peine                    25.6   
3               Peine -> Vöhrum                    30.4   
4         Vöhrum -> Hämelerwald                    35.0   

   cumulative_energy_kwh  cumulative_min  
0                      0               0  
1                    166               8  
2                    217              13  
3                    245              15  
4                    273              18

In [56]:
route_df["between_distance_km"] = route_df["cumulative_distance_km"].diff().round(2)
route_df["between_energy_kwh"] = route_df["cumulative_energy_kwh"].diff()
route_df["between_min"] = route_df["cumulative_min"].diff()
route_df["between_distance_km"].fillna(0, inplace=True)
route_df["between_energy_kwh"].fillna(0, inplace=True)
route_df["between_min"].fillna(0, inplace=True)

In [57]:
route_df.head()

source_lat  source_lng  target_lat  target_lng  \
0   52.252218   10.540295   52.252218   10.540295   
1   52.252218   10.540295   52.257212   10.359760   
2   52.257212   10.359760   52.318942   10.232145   
3   52.318942   10.232145   52.335731   10.167325   
4   52.335731   10.167325   52.354704   10.110601   

                        from_to  cumulative_distance_km  \
0              Braunschweig Hbf                     0.0   
1  Braunschweig Hbf -> Vechelde                    15.0   
2             Vechelde -> Peine                    25.6   
3               Peine -> Vöhrum                    30.4   
4         Vöhrum -> Hämelerwald                    35.0   

   cumulative_energy_kwh  cumulative_min  between_distance_km  \
0                      0               0                  0.0   
1                    166               8                 15.0   
2                    217              13                 10.6   
3                    245              15                  4.8   
4                    273              18                  4.6   

   between_energy_kwh  between_min  
0                 0.0          0.0  
1               166.0          8.0  
2                51.0          5.0  
3                28.0          2.0  
4                28.0          3.0

In [58]:
config = {'version': 'v1',
 'config': {'visState': {
   'layers': [{
     'type': 'arc',
     'config': {'dataId': 'route',
      'label': 'source -> target arc',
      'color': [201, 0, 0],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat0': 'source_lat',
       'lng0': 'source_lng',
       'lat1': 'target_lat',
       'lng1': 'target_lng'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 6.7,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'sizeRange': [0, 10],
       'targetColor': [155, 165, 46]},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear'}},
    {
     'type': 'point',
     'config': {'dataId': 'bahnhof',
      'label': 'Point',
      'color': [18, 92, 119],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat': 'latitude', 'lng': 'longitude', 'altitude': None},
      'isVisible': True,
      'visConfig': {'radius': 10,
       'fixedRadius': False,
       'opacity': 0.09,
       'outline': False,
       'thickness': 2,
       'strokeColor': None,
       'colorRange': {'name': 'Uber Viz Qualitative 4',
        'type': 'qualitative',
        'category': 'Uber',
        'colors': ['#12939A',
         '#DDB27C',
         '#88572C',
         '#FF991F',
         '#F15C17',
         '#223F9A',
         '#DA70BF',
         '#125C77',
         '#4DC19C',
         '#776E57',
         '#17B8BE',
         '#F6D18A',
         '#B7885E',
         '#FFCB99',
         '#F89570',
         '#829AE3',
         '#E79FD5',
         '#1E96BE',
         '#89DAC1',
         '#B3AD9E']},
       'strokeColorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'radiusRange': [0, 50],
       'filled': True},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': {'name': 'state', 'type': 'string'},
      'colorScale': 'ordinal',
      'strokeColorField': None,
      'strokeColorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear'}},
    {
     'type': 'point',
     'config': {'dataId': 'route',
      'label': 'target',
      'color': [19, 164, 171],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat': 'target_lat', 'lng': 'target_lng', 'altitude': None},
      'isVisible': True,
      'visConfig': {'radius': 21.1,
       'fixedRadius': False,
       'opacity': 0.91,
       'outline': False,
       'thickness': 2,
       'strokeColor': None,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'strokeColorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'radiusRange': [0, 50],
       'filled': True},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'strokeColorField': None,
      'strokeColorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear'}}],
   'interactionConfig': {'tooltip': {'fieldsToShow': {'bahnhof': [{'name': 'EVA_NR',
        'format': None},
       {'name': 'DS100', 'format': None},
       {'name': 'NAME', 'format': None},
       {'name': 'Verkehr', 'format': None},
       {'name': 'state', 'format': None}],
      'route': [{'name': 'from_to', 'format': None},
       {'name': 'cumulative_distance_km', 'format': None},
       {'name': 'cumulative_energy_kwh', 'format': None},
       {'name': 'cumulative_min', 'format': None},
       {'name': 'between_distance_km', 'format': None},
       {'name': 'between_energy_kwh', 'format': None},
       {'name': 'between_min', 'format': None}]},
     'compareMode': False,
     'compareType': 'absolute',
     'enabled': True},
    'brush': {'size': 0.5, 'enabled': False},
    'geocoder': {'enabled': False},
    'coordinate': {'enabled': False}},
   'layerBlending': 'normal',
   'splitMaps': [],
   'animationConfig': {'currentTime': None, 'speed': 1}}
}}

In [59]:
map_1 = KeplerGl(height=800, data={"bahnhof": bahnhof, "route": route_df}, config=config)
from IPython.display import Javascript
display(Javascript('''
  google.colab.widgets.installCustomManager('https://ssl.gstatic.com/colaboratory-static/widgets/colab-cdn-widget-manager/6a14374f468a145a/manager.min.js');
'''))

map_1

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<IPython.core.display.Javascript object>

KeplerGl(config={'version': 'v1', 'config': {'visState': {'layers': [{'type': 'arc', 'config': {'dataId': 'rou…

In [60]:
map_1.config

{'version': 'v1',
 'config': {'visState': {'layers': [{'type': 'arc',
     'config': {'dataId': 'route',
      'label': 'source -> target arc',
      'color': [201, 0, 0],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat0': 'source_lat',
       'lng0': 'source_lng',
       'lat1': 'target_lat',
       'lng1': 'target_lng'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 6.7,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'sizeRange': [0, 10],
       'targetColor': [155, 165, 46]},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale':

In [61]:
target_location = "Berlin Hbf"
travel_date = "2022-11-07"

In [62]:
def search_location(location):

    headers = {
    'DB-Client-Id': Client_Id,
    'DB-Api-Key': Api_Key,
    'accept': "application/json"
    }

    #print (data)

    r = requests.get(f'https://apis.deutschebahn.com/db-api-marketplace/apis/fahrplan/v1/location/{location}', headers=headers)

    r_json = r.json()

    for s in r_json:
        if s["name"] == location:
            return s

    #return r.json()

location = search_location(target_location)
location

{'name': 'Berlin Hbf', 'lon': 13.369549, 'lat': 52.525589, 'id': 8011160}

In [63]:
def journey_detail(detailsId, from_station):
    headers = {
    'DB-Client-Id': Client_Id,
    'DB-Api-Key': Api_Key,
    'accept': "application/json"
    }

    
    r = requests.get(f'https://apis.deutschebahn.com/db-api-marketplace/apis/fahrplan/v1/journeyDetails/{detailsId}', headers=headers)
    #r.encoding = 'utf-8'
    r_json = r.json()
    print (r_json)
    stations = {}
    begin_recording = False
    for t in r_json:
        #print (detailsId)
        #print (t)
        if from_station in t["stopName"]:

            begin_recording = True
        
        if begin_recording == True:
            if "&#x0028;" in  t["stopName"]:
                 t["stopName"] = t["stopName"].replace("&#x0028;", '(')
            if "&#x0029;" in t["stopName"]:
                 t["stopName"] = t["stopName"].replace("&#x0029;", ')')
            #print (t)
            arrTime = None
            depTime = None

            if "depTime" in t:
                depTime = t["depTime"]

            if "arrTime" in t:
                arrTime = t["arrTime"]
            stations[t["stopId"]] = {"lat": float(t["lat"]), "lon": float(t["lon"]), "stopName": t["stopName"], "train": t["train"],  "type": t["type"], "arrTime": arrTime, "depTime": depTime}
        
    return stations

#journey_detail("522507~186210~941230~296446~80_2022-11-07", "Berlin Hbf")

In [64]:
def depart_from(location_id, date):
    headers = {
    'DB-Client-Id': Client_Id,
    'DB-Api-Key': Api_Key,
    'accept': "application/json"
    }

    #print (data)

    trains = {}
    for h in range(24):
        #print (f"{date}T{str(h).zfill(2)}:00")
        r = requests.get(f'https://apis.deutschebahn.com/db-api-marketplace/apis/fahrplan/v1/departureBoard/{location_id}?date={date}T{str(h).zfill(2)}:00', headers=headers)

        r_json = r.json()
        #print (r_json)
        for t in r_json:
            train_date = datetime.strptime(t["dateTime"], '%Y-%m-%dT%H:%M').date()
            my_date = datetime.strptime(date, '%Y-%m-%d').date()
            #print (t)
            if train_date == my_date:
                trains[t["detailsId"]] = {"name": t["name"], "type": t["type"], "direction": t["direction"], "dateTime": t["dateTime"], "boardId": t["boardId"]}

    return trains

#journey = depart_from(location["id"], travel_date)

In [65]:
def arrive_at(location_id, date):
    headers = {
    'DB-Client-Id': Client_Id,
    'DB-Api-Key': Api_Key,
    'accept': "application/json"
    }

    #print (data)

    trains = {}
    for h in range(24):
        #print (f"{date}T{str(h).zfill(2)}:00")
        r = requests.get(f'https://apis.deutschebahn.com/db-api-marketplace/apis/fahrplan/v1/arrivalBoard/{location_id}?date={date}T{str(h).zfill(2)}:00', headers=headers)

        r_json = r.json()
        #print (r_json)
        for t in r_json:
            train_date = datetime.strptime(t["dateTime"], '%Y-%m-%dT%H:%M').date()
            my_date = datetime.strptime(date, '%Y-%m-%d').date()
            #print (t)
            if train_date == my_date:
                trains[t["detailsId"]] = {"name": t["name"], "type": t["type"], "origin": t["origin"], "dateTime": t["dateTime"], "boardId": t["boardId"]}

    return trains



In [66]:
journey = arrive_at(location["id"], travel_date)

In [67]:
journey

{'187515~80374~858838~366914~80_2022-11-07': {'name': 'ICE 947',
  'type': 'ICE',
  'origin': 'Düsseldorf Hbf',
  'dateTime': '2022-11-07T00:26',
  'boardId': 8011160},
 '670056~241583~536128~44712~80_2022-11-07': {'name': 'ICE 957',
  'type': 'ICE',
  'origin': 'Köln Hbf',
  'dateTime': '2022-11-07T00:26',
  'boardId': 8011160},
 '450453~167309~269720~15291~80_2022-11-07': {'name': 'ICE 907',
  'type': 'ICE',
  'origin': 'Hamburg-Altona',
  'dateTime': '2022-11-07T00:54',
  'boardId': 8098160},
 '912927~317746~162498~223060~80_2022-11-07': {'name': 'ICE 657',
  'type': 'ICE',
  'origin': 'Aachen Hbf',
  'dateTime': '2022-11-07T01:14',
  'boardId': 8011160},
 '322437~128284~473564~129303~80_2022-11-07': {'name': 'ICE 292',
  'type': 'ICE',
  'origin': 'Zürich HB',
  'dateTime': '2022-11-07T01:27',
  'boardId': 8011160},
 '287934~105257~416238~112141~80_2022-11-07': {'name': 'ICE 4',
  'type': 'ICE',
  'origin': 'Basel SBB',
  'dateTime': '2022-11-07T03:49',
  'boardId': 8098160},
 '503

In [68]:
#'205254~71184~400474~131819~80_2022-11-07': {'name': 'IC 1178',
#  'type': 'IC',
#  'direction': 'Kiel Hbf',
#  'dateTime': '2022-11-07T17:06',
#  'boardId': 8098160}

content = "train,station,source_lat,source_lng,target_lat,target_lng,arrTime\n"

for j in journey:
    try:
        details = journey_detail(j, journey[j]["origin"])

        line = ""
        for d in details:
            if str(location["lat"]) != str(details[d]["lat"]) and str(location["lon"]) != str(details[d]["lon"]):
                line = ",".join([details[d]["train"], details[d]["stopName"], str(details[d]["lat"]), str(details[d]["lon"]), str(location["lat"]), str(location["lon"]), str(details[d]["arrTime"])])
                content += line + "\n"
    except:
        pass

#print (content)

{'errorCode': 501002, 'title': 'Service Unavailable', 'detail': 'Unfortunately there was no route found. Perhaps your start or destination is not served at all or with the selected means of transport on the required date/time (e. g. sometimes stops/stations are not served on weekends).', 'status': 'SERVICE_UNAVAILABLE', 'traceId': 'b6353ddc-33fe-4186-ab57-6ae559a139dc', 'spanId': 'aa8681c0-b99d-418c-95c0-860667060956'}
{'errorCode': 501002, 'title': 'Service Unavailable', 'detail': 'Unfortunately there was no route found. Perhaps your start or destination is not served at all or with the selected means of transport on the required date/time (e. g. sometimes stops/stations are not served on weekends).', 'status': 'SERVICE_UNAVAILABLE', 'traceId': '2bbae5d3-697f-4ada-9261-ae3549cedd1b', 'spanId': '6d4d5f92-0bf4-45da-85de-f6ed528b6863'}
{'errorCode': 501002, 'title': 'Service Unavailable', 'detail': 'Unfortunately there was no route found. Perhaps your start or destination is not served a

In [69]:
with open("data/arrive_berlin.csv", 'w') as output:
    output.write(content)

In [70]:
train_paths = pd.read_csv("data/arrive_berlin.csv")

train_paths = train_paths.drop_duplicates(["train", "station", "arrTime"])

train_paths.head()

train        station  source_lat  source_lng  target_lat  target_lng  \
0  IC 94       Wien Hbf   48.184923   16.375865   52.525589   13.369549   
1  IC 94  Wien Meidling   48.174451   16.333085   52.525589   13.369549   
2  IC 94  St.Pölten Hbf   48.208304   15.624672   52.525589   13.369549   
3  IC 94       Linz Hbf   48.290178   14.292129   52.525589   13.369549   
4  IC 94       Wels Hbf   48.166082   14.026570   52.525589   13.369549   

  arrTime  
0    None  
1   19:20  
2   19:45  
3   20:34  
4   20:48

In [71]:
value_count_df = train_paths["station"].value_counts().rename_axis('station').reset_index(name='counts')

In [72]:
value_count_df.head()

station  counts
0  Berlin Südkreuz     100
1   Berlin-Spandau      82
2       Erfurt Hbf      60
3      Hamburg Hbf      59
4   Hamburg-Altona      56

In [73]:
value_count_df[value_count_df["station"] == "Saarbrücken Hbf"]

station  counts
114  Saarbrücken Hbf       2

In [74]:
train_paths = train_paths.drop(["train", "arrTime"], axis=1).drop_duplicates(subset="station").merge(value_count_df, on="station")



In [75]:
train_paths.head()

station  source_lat  source_lng  target_lat  target_lng  counts
0       Wien Hbf   48.184923   16.375865   52.525589   13.369549       6
1  Wien Meidling   48.174451   16.333085   52.525589   13.369549       5
2  St.Pölten Hbf   48.208304   15.624672   52.525589   13.369549       4
3       Linz Hbf   48.290178   14.292129   52.525589   13.369549       4
4       Wels Hbf   48.166082   14.026570   52.525589   13.369549       2

In [76]:
config_2 = {'version': 'v1',
 'config': {'visState': {'filters': [],
   'layers': [{
     'type': 'arc',
     'config': {'dataId': 'paths',
      'label': 'source -> target arc',
      'color': [146, 38, 198],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat0': 'source_lat',
       'lng0': 'source_lng',
       'lat1': 'target_lat',
       'lng1': 'target_lng'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 2,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'sizeRange': [2.2, 20.1],
       'targetColor': [195, 208, 57]},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'sizeField': {'name': 'counts', 'type': 'integer'},
      'sizeScale': 'linear'}},
    {
     'type': 'point',
     'config': {'dataId': 'paths',
      'label': 'source',
      'color': [221, 178, 124],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat': 'source_lat', 'lng': 'source_lng', 'altitude': None},
      'isVisible': True,
      'visConfig': {'radius': 10,
       'fixedRadius': False,
       'opacity': 1,
       'outline': False,
       'thickness': 2,
       'strokeColor': None,
       'colorRange': {'name': 'ColorBrewer YlGn-5',
        'type': 'sequential',
        'category': 'ColorBrewer',
        'colors': ['#ffffcc', '#c2e699', '#78c679', '#31a354', '#006837']},
       'strokeColorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'radiusRange': [0, 50],
       'filled': True},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'strokeColorField': None,
      'strokeColorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear'}}],
   'interactionConfig': {'tooltip': {'fieldsToShow': {'paths': [{'name': 'station',
        'format': None},
       {'name': 'counts', 'format': None}]},
     'compareMode': False,
     'compareType': 'absolute',
     'enabled': True},
    'brush': {'size': 0.5, 'enabled': False},
    'geocoder': {'enabled': False},
    'coordinate': {'enabled': False}},
   'layerBlending': 'normal',
   'splitMaps': [],
   'animationConfig': {'currentTime': None, 'speed': 1}},
  'mapState': {'bearing': 0,
   'dragRotate': False,
   'latitude': 50.465655456537085,
   'longitude': 11.508033999287717,
   'pitch': 0,
   'zoom': 5.31664936981374,
   'isSplit': False},
  'mapStyle': {'styleType': 'dark',
   'topLayerGroups': {},
   'visibleLayerGroups': {'label': True,
    'road': True,
    'border': False,
    'building': True,
    'water': True,
    'land': True,
    '3d building': False},
   'threeDBuildingColor': [9.665468314072013,
    17.18305478057247,
    31.1442867897876],
   'mapStyles': {}}}}

In [77]:
map_2 = KeplerGl(height=800, data={"paths": train_paths}, config=config_2)
from IPython.display import Javascript
display(Javascript('''
  google.colab.widgets.installCustomManager('https://ssl.gstatic.com/colaboratory-static/widgets/colab-cdn-widget-manager/6a14374f468a145a/manager.min.js');
'''))

map_2

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<IPython.core.display.Javascript object>

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'type': 'arc', 'config': …

In [78]:
map_2.config

{'version': 'v1',
 'config': {'visState': {'filters': [],
   'layers': [{'type': 'arc',
     'config': {'dataId': 'paths',
      'label': 'source -> target arc',
      'color': [146, 38, 198],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat0': 'source_lat',
       'lng0': 'source_lng',
       'lat1': 'target_lat',
       'lng1': 'target_lng'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 2,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'sizeRange': [2.2, 20.1],
       'targetColor': [195, 208, 57]},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': No

In [79]:
train_paths["station"].value_counts()

Wien Hbf                      1
Hanau Hbf                     1
Usti nad Labem hl.n.          1
Decin hl.n.                   1
Bad Schandau                  1
                             ..
Hannover Messe/Laatzen        1
Eisenach                      1
Gotha                         1
Hamburg-Bergedorf             1
Berlin Zoologischer Garten    1
Name: station, Length: 237, dtype: int64

Stations that can be reached from Berlin directly

In [80]:
journey = depart_from(location["id"], travel_date)

In [81]:

content = "train,station,source_lat,source_lng,target_lat,target_lng,arrTime\n"

for j in journey:
    try:
        details = journey_detail(j, target_location)

        line = ""
        for d in details:
            if str(location["lat"]) != str(details[d]["lat"]) and str(location["lon"]) != str(details[d]["lon"]):
                line = ",".join([details[d]["train"], details[d]["stopName"], str(location["lat"]), str(location["lon"]), str(details[d]["lat"]), str(details[d]["lon"]), str(details[d]["arrTime"])])
                content += line + "\n"
    except:
        pass

#print (content)

[{'train': 'IC 1950', 'stopId': 8098160, 'stopName': 'Berlin Hbf &#x0028;tief&#x0029;', 'lat': '52.525589', 'lon': '13.369549', 'depTime': '00:27', 'type': 'IC', 'operator': 'DB', 'notes': [{'key': 'PM', 'priority': '200', 'text': 'Please wear an FFP2 mask. You are legally required to do so'}, {'key': 'G ', 'priority': '260', 'text': 'Number of bicycles conveyed limited'}, {'key': 'FR', 'priority': '260', 'text': 'Bicycles conveyed - subject to reservation'}, {'key': 'KG', 'priority': '640', 'text': 'No food or beverages'}]}, {'train': 'IC 1950', 'stopId': 8011113, 'stopName': 'Berlin Südkreuz', 'lat': '52.475043', 'lon': '13.365315', 'arrTime': '00:32', 'depTime': '00:34', 'type': 'IC', 'operator': 'DB', 'notes': [{'key': 'PM', 'priority': '200', 'text': 'Please wear an FFP2 mask. You are legally required to do so'}, {'key': 'G ', 'priority': '260', 'text': 'Number of bicycles conveyed limited'}, {'key': 'FR', 'priority': '260', 'text': 'Bicycles conveyed - subject to reservation'}, {

In [82]:
with open("data/depart_berlin.csv", 'w') as output:
    output.write(content)

In [83]:
train_paths = pd.read_csv("data/depart_berlin.csv")

train_paths = train_paths.drop_duplicates(["train", "station", "arrTime"], keep= 'last')

train_paths.head()

train                     station  source_lat  source_lng  target_lat  \
0  IC 1950             Berlin Südkreuz   52.525589   13.369549   52.475043   
1  IC 1950  Lutherstadt Wittenberg Hbf   52.525589   13.369549   51.867813   
2  IC 1950                  Bitterfeld   52.525589   13.369549   51.622857   
3  IC 1950             Halle(Saale)Hbf   52.525589   13.369549   51.477510   
4  IC 1950                 Leipzig Hbf   52.525589   13.369549   51.345467   

   target_lng arrTime  
0   13.365315   00:32  
1   12.662286   01:11  
2   12.316849   01:28  
3   11.987088   01:48  
4   12.382066   02:13

In [84]:
value_count_df = train_paths["station"].value_counts().rename_axis('station').reset_index(name='counts')

value_count_df.head()

station  counts
0   Berlin-Spandau      85
1  Berlin Südkreuz      62
2     Hannover Hbf      44
3       Erfurt Hbf      44
4   Hamm(Westf)Hbf      36

In [85]:
train_paths = train_paths.drop(["train"], axis=1).drop_duplicates(subset="station").merge(value_count_df, on="station")

In [86]:
config_3 = {'version': 'v1',
 'config': {'visState': {'filters': [],
   'layers': [{
     'type': 'arc',
     'config': {'dataId': 'paths',
      'label': 'source -> target arc',
      'color': [146, 38, 198],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat0': 'source_lat',
       'lng0': 'source_lng',
       'lat1': 'target_lat',
       'lng1': 'target_lng'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 2,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'sizeRange': [2.2, 20.1],
       'targetColor': [195, 208, 57]},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'sizeField': {'name': 'counts', 'type': 'integer'},
      'sizeScale': 'linear'}},
    {
     'type': 'point',
     'config': {'dataId': 'paths',
      'label': 'target',
      'color': [221, 178, 124],
      'highlightColor': [252, 242, 26, 255],
      'columns': {'lat': 'target_lat', 'lng': 'target_lng', 'altitude': None},
      'isVisible': True,
      'visConfig': {'radius': 10,
       'fixedRadius': False,
       'opacity': 1,
       'outline': False,
       'thickness': 2,
       'strokeColor': None,
       'colorRange': {'name': 'ColorBrewer YlGn-5',
        'type': 'sequential',
        'category': 'ColorBrewer',
        'colors': ['#ffffcc', '#c2e699', '#78c679', '#31a354', '#006837']},
       'strokeColorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'radiusRange': [0, 50],
       'filled': True},
      'hidden': False,
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': None,
      'colorScale': 'quantile',
      'strokeColorField': None,
      'strokeColorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear'}}],
   'interactionConfig': {'tooltip': {'fieldsToShow': {'paths': [{'name': 'station',
        'format': None},
       {'name': 'counts', 'format': None}]},
     'compareMode': False,
     'compareType': 'absolute',
     'enabled': True},
    'brush': {'size': 0.5, 'enabled': False},
    'geocoder': {'enabled': False},
    'coordinate': {'enabled': False}},
   'layerBlending': 'normal',
   'splitMaps': [],
   'animationConfig': {'currentTime': None, 'speed': 1}},
  'mapState': {'bearing': 0,
   'dragRotate': False,
   'latitude': 50.465655456537085,
   'longitude': 11.508033999287717,
   'pitch': 0,
   'zoom': 5.31664936981374,
   'isSplit': False},
  'mapStyle': {'styleType': 'dark',
   'topLayerGroups': {},
   'visibleLayerGroups': {'label': True,
    'road': True,
    'border': False,
    'building': True,
    'water': True,
    'land': True,
    '3d building': False},
   'threeDBuildingColor': [9.665468314072013,
    17.18305478057247,
    31.1442867897876],
   'mapStyles': {}}}}

In [87]:
map_3 = KeplerGl(height=800, data={"paths": train_paths}, config=config_3)
from IPython.display import Javascript
display(Javascript('''
  google.colab.widgets.installCustomManager('https://ssl.gstatic.com/colaboratory-static/widgets/colab-cdn-widget-manager/6a14374f468a145a/manager.min.js');
'''))

map_3

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<IPython.core.display.Javascript object>

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'type': 'arc', 'config': …

In [88]:
train_paths["station"].value_counts()

Berlin Südkreuz     1
Bochnia             1
Kiel Hbf            1
Zielona Gora Gl.    1
Glogow              1
                   ..
Brno hl.n.          1
Breclav             1
Wien Hbf            1
Wien Meidling       1
Wels Hbf            1
Name: station, Length: 239, dtype: int64